In [57]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from sklearn.preprocessing import MinMaxScaler
import plotly.colors as pc
import numpy as np

# 1. DATA PROCESSING
df = pd.read_csv('athlete_events.csv')
df = df[df['Season'] == 'Summer']
df = df.dropna(subset=['Height', 'Weight', 'Age', 'Year', 'Team', 'Sport', 'Sex', 'Name']) # Added Name to dropna

# Standardize Names
team_map = {'Soviet Union': 'Russia', 'East Germany': 'Germany', 'West Germany': 'Germany',
            'Great Britain': 'UK', 'United States': 'USA'}
df['Team'] = df['Team'].replace(team_map)
df = df[(df['Year'] >= 1960) & (df['Year'] <= 2016)]

# FILTER: Top 5 Countries & Top 6 Sports
top_countries = df['Team'].value_counts().nlargest(5).index.tolist()
top_sports = ['Athletics', 'Gymnastics', 'Swimming', 'Basketball', 'Rowing', 'Cycling']

df = df[df['Team'].isin(top_countries) & df['Sport'].isin(top_sports)]
top_countries.sort()
top_sports.sort()

# SPLIT BY GENDER
df_male = df[df['Sex'] == 'M']
df_female = df[df['Sex'] == 'F']

# 2. DATA PRE-CALCULATION
# A. Radar Data (Returns Scaled AND Raw data)
def get_radar_data(d):
    g = d.groupby(['Year', 'Team']).agg({
        'Height': 'mean', 'Weight': 'mean', 'Age': 'mean',
        'Sport': 'nunique', 'ID': 'count'
    }).reset_index()
    
    # Keep raw values for tooltips
    g_raw = g.copy()
    
    scaler = MinMaxScaler()
    cols = ['Height', 'Weight', 'Age', 'Sport', 'ID']
    if not g.empty:
        g[cols] = scaler.fit_transform(g[cols])
        
    return g, g_raw

radar_male, radar_male_raw = get_radar_data(df_male)
radar_female, radar_female_raw = get_radar_data(df_female)
radar_cats = ['Height', 'Weight', 'Age', 'Versatility', 'Team Size', 'Height']

# B. Medal Data (Separated by Gender)
# Male
medals_df_m = df_male.dropna(subset=['Medal'])
mc_all_m = medals_df_m.groupby(['Year', 'Team']).size().reset_index(name='Count')
mc_sport_m = medals_df_m.groupby(['Year', 'Team', 'Sport']).size().reset_index(name='Count')

# Female
medals_df_f = df_female.dropna(subset=['Medal'])
mc_all_f = medals_df_f.groupby(['Year', 'Team']).size().reset_index(name='Count')
mc_sport_f = medals_df_f.groupby(['Year', 'Team', 'Sport']).size().reset_index(name='Count')

years = sorted(df['Year'].unique())
full_grid_all = pd.MultiIndex.from_product([years, top_countries], names=['Year', 'Team'])
full_grid_sport = pd.MultiIndex.from_product([years, top_countries, top_sports], names=['Year', 'Team', 'Sport'])

# Reindex all
mc_all_m = mc_all_m.set_index(['Year', 'Team']).reindex(full_grid_all, fill_value=0).reset_index()
mc_sport_m = mc_sport_m.set_index(['Year', 'Team', 'Sport']).reindex(full_grid_sport, fill_value=0).reset_index()
mc_all_f = mc_all_f.set_index(['Year', 'Team']).reindex(full_grid_all, fill_value=0).reset_index()
mc_sport_f = mc_sport_f.set_index(['Year', 'Team', 'Sport']).reindex(full_grid_sport, fill_value=0).reset_index()

# 3. LAYOUT SETUP
fig = make_subplots(
    rows=2, cols=2,
    specs=[[{'type': 'polar'}, {'type': 'xy'}], 
           [{'type': 'xy', 'colspan': 2}, None]],
    row_heights=[0.5, 0.5],
    vertical_spacing=0.15,
    horizontal_spacing=0.1,
    subplot_titles=("<b>National Strategy</b> (Radar)", "<b>Medal Trends</b>", "<b>Physiology</b> (Scatter)")
)

# Colors
country_colors = pc.qualitative.Prism
sport_colors = {sport: pc.qualitative.Bold[i % len(pc.qualitative.Bold)] for i, sport in enumerate(top_sports)}

# 4. INITIALIZE TRACES
start_year = 1960
n_countries = len(top_countries)
n_sports = len(top_sports)

# A. RADAR TRACES (Added customdata and hovertemplate)
# Radar M
for i, team in enumerate(top_countries):
    # Normalized Data
    row = radar_male[(radar_male['Year'] == start_year) & (radar_male['Team'] == team)]
    r_vals = row.iloc[0][['Height', 'Weight', 'Age', 'Sport', 'ID']].tolist() if not row.empty else [0]*5
    r_vals += [r_vals[0]]
    
    # Raw Data for Tooltip
    row_raw = radar_male_raw[(radar_male_raw['Year'] == start_year) & (radar_male_raw['Team'] == team)]
    r_raw = row_raw.iloc[0][['Height', 'Weight', 'Age', 'Sport', 'ID']].tolist() if not row_raw.empty else [0]*5
    r_raw += [r_raw[0]]
    
    fig.add_trace(go.Scatterpolar(
        r=r_vals, 
        theta=radar_cats, 
        name=f"{team} (M)", 
        fill='none', 
        line=dict(width=2, color=country_colors[i]), 
        showlegend=False, 
        visible=True,
        customdata=r_raw,
        hovertemplate="<b>%{theta}</b><br>Value: %{customdata:.2f}<extra></extra>"
    ), row=1, col=1)

# Radar F
for i, team in enumerate(top_countries):
    row = radar_female[(radar_female['Year'] == start_year) & (radar_female['Team'] == team)]
    r_vals = row.iloc[0][['Height', 'Weight', 'Age', 'Sport', 'ID']].tolist() if not row.empty else [0]*5
    r_vals += [r_vals[0]]
    
    row_raw = radar_female_raw[(radar_female_raw['Year'] == start_year) & (radar_female_raw['Team'] == team)]
    r_raw = row_raw.iloc[0][['Height', 'Weight', 'Age', 'Sport', 'ID']].tolist() if not row_raw.empty else [0]*5
    r_raw += [r_raw[0]]

    fig.add_trace(go.Scatterpolar(
        r=r_vals, 
        theta=radar_cats, 
        name=f"{team} (F)", 
        fill='none', 
        line=dict(width=2, dash='dot', color=country_colors[i]), 
        showlegend=False, 
        visible=False,
        customdata=r_raw,
        hovertemplate="<b>%{theta}</b><br>Value: %{customdata:.2f}<extra></extra>"
    ), row=1, col=1)

# B. MEDAL TRACES
# 1. Male All (Grey, Color, Marker)
for i, team in enumerate(top_countries):
    m_data = mc_all_m[mc_all_m['Team'] == team]
    fig.add_trace(go.Scatter(x=m_data['Year'], y=m_data['Count'], mode='lines', line=dict(color='lightgrey', width=2), opacity=0.5, showlegend=False, visible=False), row=1, col=2)
for i, team in enumerate(top_countries):
    m_data = mc_all_m[mc_all_m['Team'] == team]
    fig.add_trace(go.Scatter(x=m_data['Year'], y=m_data['Count'], mode='lines', line=dict(color=country_colors[i], width=3), name=f"{team} (Medals M)", showlegend=False, visible=True), row=1, col=2)
for i, team in enumerate(top_countries):
    m_data = mc_all_m[(mc_all_m['Team'] == team) & (mc_all_m['Year'] == start_year)]
    y_val = m_data['Count'].values[0] if not m_data.empty else 0
    fig.add_trace(go.Scatter(x=[start_year], y=[y_val], mode='markers', marker=dict(color=country_colors[i], size=8, line=dict(width=1, color='white')), showlegend=False, visible=True), row=1, col=2)

# 2. Male Sport (Grey, Color, Marker per sport)
for sport in top_sports:
    for i, team in enumerate(top_countries): # Grey
        m_data = mc_sport_m[(mc_sport_m['Team'] == team) & (mc_sport_m['Sport'] == sport)]
        fig.add_trace(go.Scatter(x=m_data['Year'], y=m_data['Count'], mode='lines', line=dict(color='lightgrey', width=2), opacity=0.5, showlegend=False, visible=False), row=1, col=2)
    for i, team in enumerate(top_countries): # Color
        m_data = mc_sport_m[(mc_sport_m['Team'] == team) & (mc_sport_m['Sport'] == sport)]
        fig.add_trace(go.Scatter(x=m_data['Year'], y=m_data['Count'], mode='lines', line=dict(color=country_colors[i], width=3), name=f"{team} ({sport} M)", showlegend=False, visible=False), row=1, col=2)
    for i, team in enumerate(top_countries): # Marker
        m_data = mc_sport_m[(mc_sport_m['Team'] == team) & (mc_sport_m['Sport'] == sport) & (mc_sport_m['Year'] == start_year)]
        y_val = m_data['Count'].values[0] if not m_data.empty else 0
        fig.add_trace(go.Scatter(x=[start_year], y=[y_val], mode='markers', marker=dict(color=country_colors[i], size=8, line=dict(width=1, color='white')), showlegend=False, visible=False), row=1, col=2)

# 3. Female All (Grey, Color, Marker)
for i, team in enumerate(top_countries):
    m_data = mc_all_f[mc_all_f['Team'] == team]
    fig.add_trace(go.Scatter(x=m_data['Year'], y=m_data['Count'], mode='lines', line=dict(color='lightgrey', width=2), opacity=0.5, showlegend=False, visible=False), row=1, col=2)
for i, team in enumerate(top_countries):
    m_data = mc_all_f[mc_all_f['Team'] == team]
    fig.add_trace(go.Scatter(x=m_data['Year'], y=m_data['Count'], mode='lines', line=dict(color=country_colors[i], width=3), name=f"{team} (Medals F)", showlegend=False, visible=False), row=1, col=2)
for i, team in enumerate(top_countries):
    m_data = mc_all_f[(mc_all_f['Team'] == team) & (mc_all_f['Year'] == start_year)]
    y_val = m_data['Count'].values[0] if not m_data.empty else 0
    fig.add_trace(go.Scatter(x=[start_year], y=[y_val], mode='markers', marker=dict(color=country_colors[i], size=8, line=dict(width=1, color='white')), showlegend=False, visible=False), row=1, col=2)

# 4. Female Sport (Grey, Color, Marker per sport)
for sport in top_sports:
    for i, team in enumerate(top_countries): # Grey
        m_data = mc_sport_f[(mc_sport_f['Team'] == team) & (mc_sport_f['Sport'] == sport)]
        fig.add_trace(go.Scatter(x=m_data['Year'], y=m_data['Count'], mode='lines', line=dict(color='lightgrey', width=2), opacity=0.5, showlegend=False, visible=False), row=1, col=2)
    for i, team in enumerate(top_countries): # Color
        m_data = mc_sport_f[(mc_sport_f['Team'] == team) & (mc_sport_f['Sport'] == sport)]
        fig.add_trace(go.Scatter(x=m_data['Year'], y=m_data['Count'], mode='lines', line=dict(color=country_colors[i], width=3), name=f"{team} ({sport} F)", showlegend=False, visible=False), row=1, col=2)
    for i, team in enumerate(top_countries): # Marker
        m_data = mc_sport_f[(mc_sport_f['Team'] == team) & (mc_sport_f['Sport'] == sport) & (mc_sport_f['Year'] == start_year)]
        y_val = m_data['Count'].values[0] if not m_data.empty else 0
        fig.add_trace(go.Scatter(x=[start_year], y=[y_val], mode='markers', marker=dict(color=country_colors[i], size=8, line=dict(width=1, color='white')), showlegend=False, visible=False), row=1, col=2)

# C. SCATTER TRACES (Added Name to tooltips)
for team in top_countries:
    for sport in top_sports:
        s_data = df_male[(df_male['Year'] == start_year) & (df_male['Team'] == team) & (df_male['Sport'] == sport)]
        fig.add_trace(go.Scatter(
            x=s_data['Weight'], 
            y=s_data['Height'], 
            mode='markers', 
            marker=dict(size=6, opacity=0.7, color=sport_colors[sport], symbol='circle'), 
            text=s_data['Name'], # Athlete Name
            hovertemplate="<b>%{text}</b><br>"+ team +"<br>"+ sport +"<br>H: %{y} cm<br>W: %{x} kg<extra></extra>",
            showlegend=False, 
            visible=True
        ), row=2, col=1)

for team in top_countries:
    for sport in top_sports:
        s_data = df_female[(df_female['Year'] == start_year) & (df_female['Team'] == team) & (df_female['Sport'] == sport)]
        fig.add_trace(go.Scatter(
            x=s_data['Weight'], 
            y=s_data['Height'], 
            mode='markers', 
            marker=dict(size=6, opacity=0.7, color=sport_colors[sport], symbol='circle-open'), 
            text=s_data['Name'], # Athlete Name
            hovertemplate="<b>%{text}</b><br>"+ team +"<br>"+ sport +"<br>H: %{y} cm<br>W: %{x} kg<extra></extra>",
            showlegend=False, 
            visible=False
        ), row=2, col=1)

# D. LEGENDS
for i, team in enumerate(top_countries):
    fig.add_trace(go.Scatter(x=[None], y=[None], mode='lines', line=dict(color=country_colors[i], width=3), name=team, legendgroup="Countries", legendgrouptitle_text="<b>Countries</b>", showlegend=True, visible=True))
for sport in top_sports:
    fig.add_trace(go.Scatter(x=[None], y=[None], mode='markers', marker=dict(color=sport_colors[sport], size=10), name=sport, legendgroup="Sports", legendgrouptitle_text="<b>Sports</b>", showlegend=True, visible=True))
fig.add_trace(go.Scatter(x=[None], y=[None], mode='lines+markers', line=dict(color='gray', width=2), marker=dict(color='gray', size=8, symbol='circle'), name="Male", legendgroup="Gender", legendgrouptitle_text="<b>Gender</b>", showlegend=True, visible=True))
fig.add_trace(go.Scatter(x=[None], y=[None], mode='lines+markers', line=dict(color='gray', width=2, dash='dot'), marker=dict(color='gray', size=8, symbol='circle-open', line=dict(width=2)), name="Female", legendgroup="Gender", showlegend=True, visible=True))

# 5. ANIMATION FRAMES (Including raw values and names in frames)
frames = []
for year in years:
    frame_data = []
    
    # 1. Radar M & F
    curr_rm = radar_male[radar_male['Year'] == year]
    curr_rf = radar_female[radar_female['Year'] == year]
    curr_rm_raw = radar_male_raw[radar_male_raw['Year'] == year]
    curr_rf_raw = radar_female_raw[radar_female_raw['Year'] == year]

    for team in top_countries:
        # Norm
        row = curr_rm[curr_rm['Team'] == team]
        r = row.iloc[0][['Height', 'Weight', 'Age', 'Sport', 'ID']].tolist() if not row.empty else [0]*5
        
        # Raw
        row_raw = curr_rm_raw[curr_rm_raw['Team'] == team]
        r_raw = row_raw.iloc[0][['Height', 'Weight', 'Age', 'Sport', 'ID']].tolist() if not row_raw.empty else [0]*5
        
        frame_data.append(go.Scatterpolar(r=r+[r[0]], customdata=r_raw+[r_raw[0]]))

    for team in top_countries:
        # Norm
        row = curr_rf[curr_rf['Team'] == team]
        r = row.iloc[0][['Height', 'Weight', 'Age', 'Sport', 'ID']].tolist() if not row.empty else [0]*5

        # Raw
        row_raw = curr_rf_raw[curr_rf_raw['Team'] == team]
        r_raw = row_raw.iloc[0][['Height', 'Weight', 'Age', 'Sport', 'ID']].tolist() if not row_raw.empty else [0]*5

        frame_data.append(go.Scatterpolar(r=r+[r[0]], customdata=r_raw+[r_raw[0]]))

    # 2. Medal Traces
    def add_medal_frame_data(df_all, df_sport, yr):
        # All Sports
        for team in top_countries: frame_data.append(go.Scatter(x=df_all[df_all['Team']==team]['Year'], y=df_all[df_all['Team']==team]['Count']))
        for team in top_countries: frame_data.append(go.Scatter(x=df_all[df_all['Team']==team]['Year'], y=df_all[df_all['Team']==team]['Count']))
        for team in top_countries:
            m = df_all[(df_all['Team'] == team) & (df_all['Year'] == yr)]
            y_val = m['Count'].values[0] if not m.empty else 0
            frame_data.append(go.Scatter(x=[yr], y=[y_val]))
            
        # Per Sport
        for sport in top_sports:
            for team in top_countries: 
                 m = df_sport[(df_sport['Team'] == team) & (df_sport['Sport'] == sport)]
                 frame_data.append(go.Scatter(x=m['Year'], y=m['Count']))
            for team in top_countries: 
                 m = df_sport[(df_sport['Team'] == team) & (df_sport['Sport'] == sport)]
                 frame_data.append(go.Scatter(x=m['Year'], y=m['Count']))
            for team in top_countries:
                 m = df_sport[(df_sport['Team'] == team) & (df_sport['Sport'] == sport) & (df_sport['Year'] == yr)]
                 y_val = m['Count'].values[0] if not m.empty else 0
                 frame_data.append(go.Scatter(x=[yr], y=[y_val]))
                 
    add_medal_frame_data(mc_all_m, mc_sport_m, year)
    add_medal_frame_data(mc_all_f, mc_sport_f, year)

    # 3. Scatter M & F (Include Name text)
    curr_sm = df_male[df_male['Year'] == year]
    curr_sf = df_female[df_female['Year'] == year]
    for team in top_countries:
        for sport in top_sports:
            s = curr_sm[(curr_sm['Team'] == team) & (curr_sm['Sport'] == sport)]
            frame_data.append(go.Scatter(x=s['Weight'], y=s['Height'], text=s['Name']))
    for team in top_countries:
        for sport in top_sports:
            s = curr_sf[(curr_sf['Team'] == team) & (curr_sf['Sport'] == sport)]
            frame_data.append(go.Scatter(x=s['Weight'], y=s['Height'], text=s['Name']))

    # 4. Legends (Static)
    for _ in range(len(top_countries) + len(top_sports) + 2):
        frame_data.append(go.Scatter(x=[None], y=[None]))
            
    frames.append(go.Frame(data=frame_data, name=str(year)))
fig.frames = frames

# 6. INDICES
idx_rad_m = 0
idx_rad_f = n_countries 

# Medal Blocks
idx_med_m_all = 2 * n_countries # Start index
idx_med_m_sport = idx_med_m_all + (3 * n_countries)
idx_med_f_all = idx_med_m_sport + (n_sports * 3 * n_countries)
idx_med_f_sport = idx_med_f_all + (3 * n_countries)

# Scatter Blocks
idx_sca_m = idx_med_f_sport + (n_sports * 3 * n_countries)
idx_sca_f = idx_sca_m + (n_countries * n_sports)
idx_leg = idx_sca_f + (n_countries * n_sports)

total_traces = len(fig.data)

# 7. VISIBILITY LOGIC
def get_vis(show_rad_m=False, show_rad_f=False, 
            country_idx=None, sport_idx=None): 
    
    vis = [False] * total_traces
    
    # A. Radar
    if show_rad_m:
        start = idx_rad_m
        if country_idx is not None: vis[start + country_idx] = True
        else:
            for i in range(n_countries): vis[start + i] = True
    if show_rad_f:
        start = idx_rad_f
        if country_idx is not None: vis[start + country_idx] = True
        else:
            for i in range(n_countries): vis[start + i] = True
            
    # B. Medal (Dependent on Gender)
    # Helper for medal block visibility
    def enable_medal_block(start_idx, c_idx):
        # start_idx points to the block of 3N traces (Grey, Color, Marker)
        idx_g = start_idx
        idx_c = start_idx + n_countries
        idx_k = start_idx + 2 * n_countries
        
        if c_idx is not None:
             # Grey lines for context
             for i in range(n_countries): vis[idx_g + i] = True
             # Specific Country Color & Marker
             vis[idx_c + c_idx] = True
             vis[idx_k + c_idx] = True
        else:
            # All Countries Colors & Markers
            for i in range(n_countries): 
                vis[idx_c + i] = True
                vis[idx_k + i] = True
                
    if show_rad_m:
        # Male Medals
        if sport_idx is None:
            enable_medal_block(idx_med_m_all, country_idx)
        else:
            # Specific Sport Block
            # Block size = 15 (5g, 5c, 5k)
            block_start = idx_med_m_sport + (sport_idx * 15)
            enable_medal_block(block_start, country_idx)
            
    if show_rad_f:
        # Female Medals
        if sport_idx is None:
            enable_medal_block(idx_med_f_all, country_idx)
        else:
            block_start = idx_med_f_sport + (sport_idx * 15)
            enable_medal_block(block_start, country_idx)

    # C. Scatter
    def enable_scatter(start_idx, c_idx, s_idx):
        if c_idx is not None and s_idx is not None:
            vis[start_idx + (c_idx * n_sports) + s_idx] = True
        elif c_idx is not None:
            base = start_idx + (c_idx * n_sports)
            for s in range(n_sports): vis[base + s] = True
        elif s_idx is not None:
            for c in range(n_countries):
                vis[start_idx + (c * n_sports) + s_idx] = True
        else:
            for i in range(idx_sca_m, idx_sca_f): 
                if start_idx == idx_sca_m: vis[i] = True
            for i in range(idx_sca_f, idx_leg):
                if start_idx == idx_sca_f: vis[i] = True
                
    if show_rad_m: 
         enable_scatter(idx_sca_m, country_idx, sport_idx)
    if show_rad_f: 
         enable_scatter(idx_sca_f, country_idx, sport_idx)

    # D. Legends
    for i in range(idx_leg, total_traces): vis[i] = True
    
    return vis

# 8. BUTTONS
vis_male_default = get_vis(show_rad_m=True)
vis_female_default = get_vis(show_rad_f=True)

# Gender
gender_buttons = [
    dict(label="Male", method="update", args=[{"visible": vis_male_default}]),
    dict(label="Female", method="update", args=[{"visible": vis_female_default}])
]

# Country
country_buttons = []
country_buttons.append(dict(label="All Countries", method="update", args=[{"visible": vis_male_default}]))
for i, team in enumerate(top_countries):
    vis = get_vis(show_rad_m=True, country_idx=i, sport_idx=None)
    country_buttons.append(dict(label=team, method="update", args=[{"visible": vis}]))

# Sport
sport_buttons = []
sport_buttons.append(dict(label="All Sports", method="update", args=[{"visible": vis_male_default}]))
for j, sport in enumerate(top_sports):
    vis = get_vis(show_rad_m=True, country_idx=None, sport_idx=j)
    sport_buttons.append(dict(label=sport, method="update", args=[{"visible": vis}]))

# 9. LAYOUT
fig.update_layout(
    template="plotly_dark",
    height=700,
    margin=dict(t=160, b=50, l=50, r=50),
    title=dict(text="<b>The Shape of Glory: Olympics 1960 - 2016</b>", font=dict(size=24), y=0.98, x=0.05),
    xaxis=dict(title="Year", domain=[0.6, 1.0]),
    yaxis=dict(title="Medals", domain=[0.55, 1.0]),
    xaxis2=dict(title="Weight (kg)", range=[30, 160], domain=[0.0, 1.0]),
    yaxis2=dict(title="Height (cm)", range=[130, 220], domain=[0.0, 0.45]),
    polar=dict(radialaxis=dict(visible=True, range=[0, 1]), domain=dict(x=[0.0, 0.4], y=[0.55, 1.0])),
    legend=dict(x=1.02, y=0.5, tracegroupgap=20),
    updatemenus=[
        dict(type="buttons", direction="left", showactive=True, x=1.0, y=1.15, xanchor="right", yanchor="top", buttons=gender_buttons, bgcolor="#333", bordercolor="#666", borderwidth=1),
        dict(buttons=sport_buttons, direction="down", showactive=True, x=0.82, y=1.15, xanchor="right", yanchor="top", bgcolor="#333"),
        dict(buttons=country_buttons, direction="down", showactive=True, x=0.64, y=1.15, xanchor="right", yanchor="top", bgcolor="#333"),
        dict(type="buttons", direction="left", x=0.0, y=-0.10, xanchor="left", bgcolor="#333", font=dict(color="white"), bordercolor="#666", borderwidth=1, buttons=[
                {"label": "▶", "method": "animate", "args": [None, {"frame": {"duration": 1000, "redraw": True}, "fromcurrent": True}]},
                {"label": "❚❚", "method": "animate", "args": [[None], {"mode": "immediate", "transition": {"duration": 0}}]}
            ]),
        dict(type="buttons", direction="left", x=0.12, y=-0.10, xanchor="left", bgcolor="#333", font=dict(color="white"), bordercolor="#666", borderwidth=1, buttons=[
                {"label": "0.25x", "method": "animate", "args": [None, {"frame": {"duration": 2000, "redraw": True}, "fromcurrent": True}]},
                {"label": "0.5x", "method": "animate", "args": [None, {"frame": {"duration": 1000, "redraw": True}, "fromcurrent": True}]},
                {"label": "1x", "method": "animate", "args": [None, {"frame": {"duration": 500, "redraw": True}, "fromcurrent": True}]},
            ])
    ],
    sliders=[{"steps": [{"args": [[str(y)], {"frame": {"duration": 300, "redraw": True}, "mode": "immediate"}], "label": str(y), "method": "animate"} for y in years], "x": 0.35, "y": -0.10, "len": 0.6}]
)

fig.layout.annotations = []
fig.add_annotation(text="Gender:", x=1.0, y=1.22, xref="paper", yref="paper", showarrow=False, xanchor="right", font=dict(color="white", size=11))
fig.add_annotation(text="Sport:", x=0.82, y=1.22, xref="paper", yref="paper", showarrow=False, xanchor="right", font=dict(color="white", size=11))
fig.add_annotation(text="Country:", x=0.64, y=1.22, xref="paper", yref="paper", showarrow=False, xanchor="right", font=dict(color="white", size=11))
fig.add_annotation(text="Speed:", x=0.12, y=-0.06, xref="paper", yref="paper", showarrow=False, xanchor="left", font=dict(color="white", size=10))
fig.add_annotation(text="<b>National Strategy</b> (Radar)", x=0.22, y=1.08, xref="paper", yref="paper", xanchor="center", showarrow=False, font=dict(size=14, color="white")) 
fig.add_annotation(text="<b>Medal Trends</b>", x=0.8, y=1.05, xref="paper", yref="paper", showarrow=False, font=dict(size=14, color="white"))
fig.add_annotation(text="<b>Physiology</b> (Scatter)", x=0.5, y=0.48, xref="paper", yref="paper", showarrow=False, font=dict(size=14, color="white"))

fig.write_html("olympic_dashboard.html")
fig.show()